In [ ]:
%matplotlib inline


# Restart

In this tutorial, the restart functionnality of Freshkiss3D is explained.


In [ ]:
import os
import matplotlib.pylab as plt
import numpy as np
import freshkiss3d as fk
import freshkiss3d.extra.plots as fk_plt

# ~ os.system('rm -r outputs')
#sphinx_gallery_thumbnail_number = 4

## Restart scheduler: 

To enable the restart, you have to set an ``h5_writer`` and pass it to the 
``Problem`` class. Here we set the restart scheduler to time and set it to 1,2 and 3s.
At the first time set simulation will stop and create a back up save file. Saved data ara stored
inside a ``restart_data.h5`` file that allow to perform a restart of the simulation
from the time it stopped. 




<div class="alert alert-info"><h4>Note</h4><p>Restart can be performed several times in the same simulation. In our case, 
   simulation time is splitted in 4 sections, and 3 iterative restarts are performed.</p></div>




## Case set-up: 




In [ ]:
restart_times = [1., 2., 3.]
restart_scheduler = fk.schedules(times=restart_times)

simutime = fk.SimuTime(final_time=5.1, time_iteration_max=20000, second_order=True)

create_figure_scheduler = fk.schedules(times=[1., 2., 3.])

triangular_mesh = fk.TriangularMesh.from_msh_file('../simulations/inputs/square2.mesh')

layer = fk.Layer(1, triangular_mesh, topography=0.)

def H_0(x, y):
    h = 2.4*(1.0 + np.exp(-0.25*((x-10.05)**2+(y-10.05)**2)))
    return h

primitives = fk.Primitive(triangular_mesh, layer, height_funct=H_0)

tracers = [fk.Tracer(triangular_mesh, layer, primitives, Tinit=1.0)]

slides = [fk.Slide(ref=r) for r in [1, 2, 3, 4]]

h5_writer = fk.H5Writer(scheduler=restart_scheduler, \
    output_dir='outputs/hydrodynamic_h5_from_{}_to_{}'.format(\
    int(restart_times[0]), int(restart_times[-1])))

problem = fk.Problem(simutime, triangular_mesh, layer, primitives,
                     slides=slides,
                     numerical_parameters={'space_second_order':True},
                     tracers=tracers,
                     h5_writer=h5_writer,
                     custom_funct={'plot':fk_plt.plot_freesurface_3d},
                     custom_funct_scheduler=create_figure_scheduler)
RESTART = False
if RESTART:
    # computation restarts after 2 s
    problem.restart('./outputs/hydrodynamic_h5_from_1_to_3/output_0001.h5')
    restart_times = [4., 5.]
    restart_scheduler = fk.schedules(times=restart_times)
    problem.h5_writer = fk.H5Writer(scheduler=restart_scheduler, \
        output_dir='outputs/hydrodynamic_h5_from_{}_to_{}'.format(\
        int(restart_times[0]), int(restart_times[-1])))
    create_figure_scheduler = fk.schedules(times=[3., 4., 5.])
    problem.custom_funct_scheduler = create_figure_scheduler

problem.solve()
plt.show()